# Analysis Using EpiModel Package

In [1]:
# Clean Environment
rm(list = ls())
gc()

used    (Mb) gc trigger (Mb) max used (Mb)
Ncells  567694 30.4 1229577    65.7  713164  38.1
Vcells 1064924  8.2 8388608    64.0 1820463  13.9

In [3]:
# Import needed libraries
library(covid19.analytics)
library(dygraphs)
library(writexl)
library(xts)
library(deSolve)
library(reshape2)
library(EpiModel)

Loading required package: zoo


Attaching package: ‘zoo’


The following objects are masked from ‘package:base’:

    as.Date, as.Date.numeric


Loading required package: networkDynamic

Loading required package: network


‘network’ 1.17.1 (2021-06-12), part of the Statnet Project
* ‘news(package="network")’ for changes since last version
* ‘citation("network")’ for citation information
* ‘https://statnet.org’ for help, support, and other information



‘networkDynamic’ 0.11.0 (2021-06-12), part of the Statnet Project
* ‘news(package="networkDynamic")’ for changes since last version
* ‘citation("networkDynamic")’ for citation information
* ‘https://statnet.org’ for help, support, and other information


Loading required package: tergm

Loading required package: ergm


‘ergm’ 4.1.2 (2021-07-26), part of the Statnet Project
* ‘news(package="ergm")’ for changes since last version
* ‘citation("ergm")’ for citation information
* ‘https://statnet.org’ for help, support, and other information

In [3]:
# # SI Model

# param <- param.dcm(inf.prob = 0.50, act.rate = 0.14)
# init <- init.dcm(s.num = 500, i.num = 1)
# control <- control.dcm(type = "SI", nsteps = 200)
# mod <- dcm(param, init, control)
# plot(mod)

# Reference

- `si.flow` = the numver of people moving from S to I at each time step
- `ir.flow` = same as before but from I to R

## Links

- https://www.medrxiv.org/content/10.1101/2020.04.30.20086306v1.full.pdfhttps://www.medrxiv.org/content/10.1101/2020.04.30.20086306v1.full.pdf

In [7]:
# SIR model 

param <- param.dcm(inf.prob = 0.556, act.rate = 0.5, rec.rate = 1/14)

init <- init.dcm(s.num = 83e+06, i.num = 1, r.num = 0)

control <- control.dcm(type = "SIR", nsteps = 1000, dt = 1)
mod <- dcm(param, init, control)

In [8]:
SIR_out <- as.data.frame(mod)

SIR_out <- SIR_out[1:4]

# View(SIR_out)

In [9]:
dygraph(SIR_out)

HTML widgets cannot be represented in plain text (need html)

In [7]:
SEIR <- function(t, t0, parms) {
  with(as.list(c(t0, parms)), {
    
    # Population size
    num <- s.num + e.num + i.num + r.num
    
    # Effective contact rate and FOI from a rearrangement of Beta * c * D
    ce <- R0 / i.dur
    lambda <- ce * i.num/num
  
    dS <- -lambda*s.num
    dE <- lambda*s.num - (1/e.dur)*e.num
    dI <- (1/e.dur)*e.num - (1 - cfr)*(1/i.dur)*i.num - cfr*(1/i.dur)*i.num
    dR <- (1 - cfr)*(1/i.dur)*i.num
    
    # Compartments and flows are part of the derivative vector
    # Other calculations to be output are outside the vector, but within the containing list
    list(c(dS, dE, dI, dR, 
           se.flow = lambda * s.num,
           ei.flow = (1/e.dur) * e.num,
           ir.flow = (1 - cfr)*(1/i.dur) * i.num,
           d.flow = cfr*(1/i.dur)*i.num),
         num = num,
         i.prev = i.num / num,
         ei.prev = (e.num + i.num)/num)
  })
}

In [8]:
param <- param.dcm(R0 = 1.2, e.dur = 30, i.dur = 20, cfr = c(0.1, 0.5, 0.8))

init <- init.dcm(s.num = 83e+06, e.num = 100, i.num = 0, r.num = 0, se.flow = 0, ei.flow = 0, ir.flow = 0, d.flow = 0)

control <- control.dcm(nsteps = 10000, dt = 1, new.mod = SEIR)

mod <- dcm(param, init, control)

In [9]:
# par(mfrow = c(1, 2))
# plot(mod, y = "i.num", run = 2, main = "Prevalence")
# plot(mod, y = "se.flow", run = 2, main = "Incidence")

In [10]:
SEIR_out <- as.data.frame(mod)

SEIR_out <- SEIR_out[1:6]
SEIR_out <- SEIR_out[-1]

# View(SEIR_out)

In [11]:
dygraph(SEIR_out)

HTML widgets cannot be represented in plain text (need html)

In [12]:
mySEIR <- function(t, t0, parms) {
    with(as.list(c(t0, parms)), {
        
        n = s.num + e.num + i.num + r.num
        
        dS = -(beta * s.num * i.num)/n
        dE = (beta * s.num * i.num)/n - delta * e.num
        dI = delta * e.num - gamma * i.num
        dR = gamma * i.num
        
        list(c(dS, dE, dI, dR))
        
      
    })
}

In [13]:
incubation_days <- 2
recovery_days <- 50

param <- param.dcm(beta = 0.02, gamma = 1/recovery_days, delta = 1/incubation_days)

init <- init.dcm(s.num = 83e+06, e.num = 100000000, i.num = 0, r.num = 0)

control <- control.dcm(nsteps = 5000, dt = 1, new.mod = mySEIR)

mod <- dcm(param, init, control)

mod

EpiModel Simulation
Model class: dcm

Simulation Summary
-----------------------
No. runs: 1
No. time steps: 5000

Model Parameters
-----------------------
beta = 0.02
gamma = 0.02
delta = 0.5

Model Output
-----------------------
Variables: s.num e.num i.num r.num

In [14]:
mySEIR_out <- as.data.frame(mod)

head(mySEIR_out)
tail(mySEIR_out)
# View(mySEIR_out)

time s.num    e.num     i.num    r.num    
1 1    83000000 100000000        0       0.0
2 2    82807725  60841220 38926683  424372.3
3 3    82343174  37289561 61913393 1453872.3
4 4    81722319  23118763 75320031 2838887.1
5 5    81015120  14586282 82969198 4429400.0
6 6    80263437   9442839 87158469 6135255.9

time s.num    e.num        i.num        r.num    
4995 4995 37472528 7.140155e-29 8.442407e-27 145527472
4996 4996 37472528 7.028429e-29 8.310304e-27 145527472
4997 4997 37472528 6.918451e-29 8.180268e-27 145527472
4998 4998 37472528 6.810194e-29 8.052267e-27 145527472
4999 4999 37472528 6.703632e-29 7.926269e-27 145527472
5000 5000 37472528 6.598736e-29 7.802242e-27 145527472

In [15]:
dygraph(mySEIR_out)

HTML widgets cannot be represented in plain text (need html)

In [20]:
SEIOPR <- function(t, t0, parms) {
    with(as.list(c(t0, parms)), {
            num <- s.num + e.num + i.num + o.num + p.num + r.num
        
            dS <- xi * p.num - beta * i.num * s.num - nu * s.num
            dE <- beta * i.num * s.num - sigma * e.num
            dI <- sigma * e.num - delta * i.num - gamma * i.num
            dO <- gamma * i.num - omega * o.num - eta * o.num
            dP <- delta * i.num + eta * o.num + nu * s.num
            dR <- omega * o.num
        
            list(c(dS, dE, dI, dO, dP, dR),
                 num = num)
        })
    }

In [29]:
beta  <- 0.4
sigma <- 0.4
gamma <- 0.4
omega <- 0.4
delta <- 0.4
xi    <- 0.4
nu    <- 0.4
eta   <- 0.4

sus_num <- 1e6
exp_num <- 0
inf_num <- 0
osp_num <- 0
pro_num <- 0
rem_num <- 0

param <- param.dcm(beta = beta,
                   sigma = sigma,
                   gamma = gamma,
                   omega = omega,
                   delta = delta,
                   xi = xi,
                   nu = nu,
                   eta = eta)

init <- init.dcm(s.num = sus_num,
                 e.num = exp_num,
                 i.num = inf_num,
                 o.num = osp_num,
                 p.num = pro_num,
                 r.num = rem_num)

control <- control.dcm(nsteps = 1000,
                       dt = 1,
                       new.mod = SEIOPR)

mod <- dcm(param, init, control)

mod

EpiModel Simulation
Model class: dcm

Simulation Summary
-----------------------
No. runs: 1
No. time steps: 1000

Model Parameters
-----------------------
beta = 0.4
sigma = 0.4
gamma = 0.4
omega = 0.4
delta = 0.4
xi = 0.4
nu = 0.4
eta = 0.4

Model Output
-----------------------
Variables: s.num e.num i.num o.num p.num r.num num

In [30]:
SEIOPR_out <- as.data.frame(mod)

head(SEIOPR_out)
tail(SEIOPR_out)
# View(mySEIR_out)

time s.num     e.num i.num o.num p.num     r.num num    
1 1    1000000.0 0     0     0           0.0 0     1000000
2 2     733333.3 0     0     0      338133.3 0     1071467
3 3     652111.9 0     0     0      610263.0 0     1262375
4 4     684565.7 0     0     0      874377.3 0     1558943
5 5     797670.9 0     0     0     1168340.6 0     1966012
6 6     980013.6 0     0     0     1521557.1 0     2501571

time s.num         e.num i.num o.num p.num         r.num num          
995   995 1.439269e+112 0     0     0     2.328785e+112 0     3.768054e+112
996   996 1.842904e+112 0     0     0     2.981881e+112 0     4.824784e+112
997   997 2.359736e+112 0     0     0     3.818133e+112 0     6.177869e+112
998   998 3.021511e+112 0     0     0     4.888907e+112 0     7.910418e+112
999   999 3.868877e+112 0     0     0     6.259975e+112 0     1.012885e+113
1000 1000 4.953883e+112 0     0     0     8.015551e+112 0     1.296943e+113

In [31]:
dygraph(SEIOPR_out)

HTML widgets cannot be represented in plain text (need html)